In [ ]:
%%capture
import os, re
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth
else:
    # Do this only in Colab notebooks! Otherwise use pip install unsloth
    import torch; v = re.match(r"[0-9]{1,}\.[0-9]{1,}", str(torch.__version__)).group(0)
    xformers = "xformers==" + ("0.0.33.post1" if v=="2.9" else "0.0.32.post2" if v=="2.8" else "0.0.29.post3")
    !pip install --no-deps bitsandbytes accelerate {xformers} peft trl triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf "datasets==4.3.0" "huggingface_hub>=0.34.0" hf_transfer
    !pip install --no-deps unsloth
# Install transformers branch for Ministral
#!pip install git+https://github.com/huggingface/transformers.git@bf3f0ae70d0e902efab4b8517fce88f6697636ce
#!pip install --no-deps trl==0.22.2

In [ ]:
ministral_models = [
    "unsloth/Ministral-3-3B-Instruct-2512", # Ministral instruct models
    "unsloth/Ministral-3-8B-Instruct-2512",
    "unsloth/Ministral-3-14B-Instruct-2512",

    "unsloth/Ministral-3-3B-Reasoning-2512", # Ministral reasoning models
    "unsloth/Ministral-3-8B-Reasoning-2512",
    "unsloth/Ministral-3-14B-Reasoning-2512",

    "unsloth/Ministral-3-3B-Base-2512", # Ministral base models
    "unsloth/Ministral-3-8B-Base-2512",
    "unsloth/Ministral-3-14B-Base-2512",
]

fourbit_models = [
    "unsloth/Meta-Llama-3.1-8B-bnb-4bit",      # Llama-3.1 2x faster
    "unsloth/Meta-Llama-3.1-8B-Instruct-bnb-4bit",
    "unsloth/Meta-Llama-3.1-70B-bnb-4bit",
    "unsloth/Meta-Llama-3.1-405B-bnb-4bit",    # 4bit for 405b!
    "unsloth/Mistral-Small-Instruct-2409",     # Mistral 22b 2x faster!
    "unsloth/mistral-7b-instruct-v0.3-bnb-4bit",
    "unsloth/Phi-3.5-mini-instruct",           # Phi-3.5 2x faster!
    "unsloth/Phi-3-medium-4k-instruct",
    "unsloth/gemma-2-9b-bnb-4bit",
    "unsloth/gemma-2-27b-bnb-4bit",            # Gemma 2x faster!

    "unsloth/Llama-3.2-1B-bnb-4bit",           # NEW! Llama 3.2 models
    "unsloth/Llama-3.2-1B-Instruct-bnb-4bit",
    "unsloth/Llama-3.2-3B-bnb-4bit",
    "unsloth/Llama-3.2-3B-Instruct-bnb-4bit",

    "unsloth/Llama-3.3-70B-Instruct-bnb-4bit" # NEW! Llama 3.3 70B!
] # More models at https://huggingface.co/unsloth


In [ ]:
#Hyperparamters
max_seq_length = 2048
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit to reduce memory use. False for 16bit LoRA.
#load_in_8bit = False # Use 8bit quantization to reduce memory usage. Can be False.
epoch = 1
MODEL_ID = "unsloth/Llama-3.2-1B-Instruct"
MODEL = "Llama-3.2-1B-Instruct"
chat_template = "llama-3.1"

#Huggingface settings
HF_USERNAME = "schmuelling"
MODEL_NAME = f"{MODEL}-finetome"

## Set up HuggingFace

In [ ]:

from huggingface_hub import login
import os

HF_TOKEN = input("Access Token: ").strip()
login(token=HF_TOKEN)

os.environ["HF_TOKEN"] = HF_TOKEN

In [ ]:
# Checkpoint repo (for training)
checkpoint_repo_id = f"{HF_USERNAME}/{MODEL_NAME}-checkpoint"

#repo (for final quantized models)
repo_id = f"{HF_USERNAME}/{MODEL_NAME}"

## Load model

In [ ]:
from unsloth import FastLanguageModel
import torch
from huggingface_hub import repo_exists
from unsloth.chat_templates import get_chat_template

# Check if checkpoint repo exists and load accordingly
if repo_exists(checkpoint_repo_id, token=HF_TOKEN):
    print(f"Loading from checkpoint: {checkpoint_repo_id}")
    model, tokenizer = FastLanguageModel.from_pretrained(
        checkpoint_repo_id,
        load_in_4bit=load_in_4bit,
        use_gradient_checkpointing = "unsloth",
        token = HF_TOKEN,
    )
    resume_training = True
else:
    print(f"Loading base model: {MODEL_ID}")
    model, tokenizer = FastLanguageModel.from_pretrained(
        MODEL_ID,
        load_in_4bit=load_in_4bit,
        use_gradient_checkpointing = "unsloth",
    )
    resume_training = False


tokenizer = get_chat_template(
    tokenizer,
    chat_template = chat_template,
)


Loading base model: unsloth/Llama-3.2-1B-Instruct
==((====))==  Unsloth 2025.11.6: Fast Llama patching. Transformers: 4.57.2.
   \\   /|    NVIDIA A100-SXM4-40GB. Num GPUs = 1. Max memory: 39.557 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.9.0+cu126. CUDA: 8.0. CUDA Toolkit: 12.6. Triton: 3.5.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.33.post1. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Add LoRA adapters.

In [ ]:
#if not resume_training:

  #  model = FastLanguageModel.get_peft_model(
  #      model,
  #      finetune_vision_layers     = False, # False if not finetuning vision layers
  #      finetune_language_layers   = True, # False if not finetuning language layers
  #      finetune_attention_modules = True, # False if not finetuning attention layers
  #      finetune_mlp_modules       = True, # False if not finetuning MLP layers
  #
 #       r = 16,           # The larger, the higher the accuracy, but might overfit
 #       lora_alpha = 16,  # Recommended alpha == r at least
 #       lora_dropout = 0,
 #       bias = "none",
 #       random_state = 3407,
 #       use_rslora = False,  # We support rank stabilized LoRA
 #       loftq_config = None, # And LoftQ
 #       # target_modules = "all-linear", # Optional now! Can specify a list if needed
 #   )



In [ ]:
if not resume_training:
  model = FastLanguageModel.get_peft_model(
    model,
    r = 16,
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

## Data Prep

In [ ]:
from unsloth.chat_templates import get_chat_template

# This cell now only defines the formatting function and loads the dataset.
# The tokenizer setup will happen after the model is loaded.

def formatting_prompts_func(examples):
    convos = examples["conversations"]
    texts = [tokenizer.apply_chat_template(convo, tokenize = False, add_generation_prompt = False) for convo in convos]
    return { "text" : texts, }
pass

from datasets import load_dataset
dataset = load_dataset("mlabonne/FineTome-100k", split = "train")

### Format from ShareGPT to HuggingFace's generic format to bring it eventually into the correspoinding chat format of the model.


```
{"from": "system", "value": "You are an assistant"}
{"from": "human", "value": "What is 2+2?"}
{"from": "gpt", "value": "It's 4."}
```
to
```
{"role": "system", "content": "You are an assistant"}
{"role": "user", "content": "What is 2+2?"}
{"role": "assistant", "content": "It's 4."}
```

In [ ]:
from unsloth.chat_templates import standardize_sharegpt
dataset = standardize_sharegpt(dataset)
dataset = dataset.map(formatting_prompts_func, batched = True,)

## Set the trainer up

In [ ]:
from trl import SFTTrainer, SFTConfig
from transformers import DataCollatorForSeq2Seq
import torch, os, gc
from unsloth import FastLanguageModel, is_bfloat16_supported


In [ ]:
from trl import SFTConfig
from unsloth import is_bfloat16_supported

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    data_collator = DataCollatorForSeq2Seq(tokenizer = tokenizer),
    dataset_num_proc = 2,
    packing = False,
    args = SFTConfig(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 20,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 5,
        save_steps = 100,
        save_total_limit = 3,
        optim = "adamw_8bit",
        weight_decay = 0.001,
        lr_scheduler_type = "linear",
        max_steps = 2000,
        num_train_epochs = 1,
        seed = 3407,
        output_dir = "outputs",
        report_to = "tensorboard",

        # HuggingFace Hub integration
        push_to_hub = True,
        hub_model_id = checkpoint_repo_id,
        hub_strategy = "checkpoint",  # push on every save
    ),
)

## Finetuning

In [ ]:
#first things first check for available GPUs

device_name = torch.cuda.get_device_name(0)
print("GPU:", device_name)
print("CUDA available:", torch.cuda.is_available())


GPU: NVIDIA A100-SXM4-40GB
CUDA available: True


In [ ]:
%load_ext tensorboard
%tensorboard --logdir outputs/logs

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


<IPython.core.display.Javascript object>

In [ ]:
if resume_training:
    print("Will resume training.")
    trainer_stats = trainer.train(resume_from_checkpoint=True)
else:
    print("Will start training from scratch.")
    trainer_stats = trainer.train()


The model is already on multiple devices. Skipping the move to device specified in `args`.


Will start training from scratch.


==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 100,000 | Num Epochs = 1 | Total steps = 2,000
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 4 x 1) = 8
 "-____-"     Trainable parameters = 11,272,192 of 1,247,086,592 (0.90% trained)


In [ ]:
# @title Show final memory and time stats
import torch

# Define max_memory:
if torch.cuda.is_available():
    max_memory = torch.cuda.get_device_properties(0).total_memory / 1024 / 1024 / 1024
else:
    # Set a default max_memory if no CUDA device is available to prevent errors
    max_memory = 16.0 # Example: 16 GB, adjust as needed for your environment


start_gpu_memory = 0.0


used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory / max_memory * 100, 3)
lora_percentage = round(used_memory_for_lora / max_memory * 100, 3)

# trainer_stats should be available from previous cell execution.
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(
    f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training."
)
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

1844.8369 seconds used for training.
30.75 minutes used for training.
Peak reserved memory = 4.477 GB.
Peak reserved memory for training = 4.477 GB.
Peak reserved memory % of max memory = 11.318 %.
Peak reserved memory for training % of max memory = 11.318 %.


## Save Model

In [ ]:
model.save_pretrained_gguf(repo_id, tokenizer, quantization_method = "q4_k_m")

Unsloth: Merging model weights to 16-bit format...
Found HuggingFace hub cache directory: /root/.cache/huggingface/hub
Checking cache directory for required files...
Cache check failed: model.safetensors not found in local cache.
Not all required files found in cache. Will proceed with downloading.
Checking cache directory for required files...
Cache check failed: tokenizer.model not found in local cache.
Not all required files found in cache. Will proceed with downloading.


Unsloth: Preparing safetensor model files: 100%|██████████| 1/1 [00:00<00:00, 10591.68it/s]


Note: tokenizer.model not found (this is OK for non-SentencePiece models)


Unsloth: Merging weights into 16bit: 100%|██████████| 1/1 [00:04<00:00,  4.76s/it]


Unsloth: Merge process complete. Saved to `/content/schmuelling/Llama-3.2-1B-Instruct-finetome`
Unsloth: Converting to GGUF format...
==((====))==  Unsloth: Conversion from HF to GGUF information
   \\   /|    [0] Installing llama.cpp might take 3 minutes.
O^O/ \_/ \    [1] Converting HF to GGUF bf16 might take 3 minutes.
\        /    [2] Converting GGUF bf16 to ['q4_k_m'] might take 10 minutes each.
 "-____-"     In total, you will have to wait at least 16 minutes.

Unsloth: llama.cpp found in the system. Skipping installation.
Unsloth: Preparing converter script...
Unsloth: [1] Converting model into bf16 GGUF format.
This might take 3 minutes...


RuntimeError: Unsloth: GGUF conversion failed: Unsloth: Failed to convert model to GGUF: Command 'python llama.cpp/unsloth_convert_hf_to_gguf.py --outfile llama-3.2-1b-instruct.BF16.gguf --outtype bf16 --split-max-size 50G schmuelling/Llama-3.2-1B-Instruct-finetome' returned non-zero exit status 1.

In [ ]:
# save to hub
model.push_to_hub_gguf(
    repo_id,
    tokenizer,
    quantization_method = ["q4_k_m"],
    token = HF_TOKEN,
)

Unsloth: Converting model to GGUF format...
Unsloth: Merging model weights to 16-bit format...


config.json:   0%|          | 0.00/894 [00:00<?, ?B/s]

Found HuggingFace hub cache directory: /root/.cache/huggingface/hub
Checking cache directory for required files...
Cache check failed: model.safetensors not found in local cache.
Not all required files found in cache. Will proceed with downloading.
Checking cache directory for required files...
Cache check failed: tokenizer.model not found in local cache.
Not all required files found in cache. Will proceed with downloading.


Unsloth: Preparing safetensor model files:   0%|          | 0/1 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/2.47G [00:00<?, ?B/s]

Unsloth: Preparing safetensor model files: 100%|██████████| 1/1 [00:06<00:00,  6.16s/it]


Note: tokenizer.model not found (this is OK for non-SentencePiece models)


Unsloth: Merging weights into 16bit: 100%|██████████| 1/1 [00:09<00:00,  9.10s/it]


Unsloth: Merge process complete. Saved to `/tmp/unsloth_gguf_oh61da00`
Unsloth: Converting to GGUF format...
==((====))==  Unsloth: Conversion from HF to GGUF information
   \\   /|    [0] Installing llama.cpp might take 3 minutes.
O^O/ \_/ \    [1] Converting HF to GGUF bf16 might take 3 minutes.
\        /    [2] Converting GGUF bf16 to ['q4_k_m'] might take 10 minutes each.
 "-____-"     In total, you will have to wait at least 16 minutes.

Unsloth: Installing llama.cpp. This might take 3 minutes...
Unsloth: Updating system package directories
Unsloth: All required system packages already installed!
Unsloth: Install llama.cpp and building - please wait 1 to 3 minutes
Unsloth: Cloning llama.cpp repository
Unsloth: Install GGUF and other packages
Unsloth: Successfully installed llama.cpp!
Unsloth: Preparing converter script...
Unsloth: [1] Converting model into bf16 GGUF format.
This might take 3 minutes...


RuntimeError: Failed to convert model to GGUF: Unsloth: GGUF conversion failed: Unsloth: Failed to convert model to GGUF: Command 'python llama.cpp/unsloth_convert_hf_to_gguf.py --outfile llama-3.2-1b-instruct.BF16.gguf --outtype bf16 --split-max-size 50G /tmp/unsloth_gguf_oh61da00' returned non-zero exit status 1.

In [ ]:
model.push_to_hub_gguf(f"{repo_id}-q8_0", tokenizer, quantization_method = "q8_0")

Unsloth: Converting model to GGUF format...
Unsloth: Merging model weights to 16-bit format...
Found HuggingFace hub cache directory: /root/.cache/huggingface/hub
Checking cache directory for required files...
Cache check failed: model.safetensors not found in local cache.
Not all required files found in cache. Will proceed with downloading.
Checking cache directory for required files...
Cache check failed: tokenizer.model not found in local cache.
Not all required files found in cache. Will proceed with downloading.


Unsloth: Preparing safetensor model files:   0%|          | 0/1 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/2.47G [00:00<?, ?B/s]

Unsloth: Preparing safetensor model files: 100%|██████████| 1/1 [00:06<00:00,  6.64s/it]


Note: tokenizer.model not found (this is OK for non-SentencePiece models)


Unsloth: Merging weights into 16bit: 100%|██████████| 1/1 [00:08<00:00,  8.42s/it]


Unsloth: Merge process complete. Saved to `/tmp/unsloth_gguf_rywkjfcu`
Unsloth: Converting to GGUF format...
==((====))==  Unsloth: Conversion from HF to GGUF information
   \\   /|    [0] Installing llama.cpp might take 3 minutes.
O^O/ \_/ \    [1] Converting HF to GGUF bf16 might take 3 minutes.
\        /    [2] Converting GGUF bf16 to ['q8_0'] might take 10 minutes each.
 "-____-"     In total, you will have to wait at least 16 minutes.

Unsloth: llama.cpp found in the system. Skipping installation.
Unsloth: Preparing converter script...
Unsloth: [1] Converting model into bf16 GGUF format.
This might take 3 minutes...


RuntimeError: Failed to convert model to GGUF: Unsloth: GGUF conversion failed: Unsloth: Failed to convert model to GGUF: Command 'python llama.cpp/unsloth_convert_hf_to_gguf.py --outfile llama-3.2-1b-instruct.BF16.gguf --outtype bf16 --split-max-size 50G /tmp/unsloth_gguf_rywkjfcu' returned non-zero exit status 1.

In [ ]:
# saving for vLLM or Transformer
model.save_pretrained_merged(repo_id, tokenizer, save_method = "merged_4bit_forced")
#model.push_to_hub_merged(repo_id, tokenizer, save_method = "merged_4bit_forced", token = HF_TOKEN)

In [ ]:
model.push_to_hub_merged(repo_id, tokenizer, save_method = "merged_4bit_forced", token = HF_TOKEN)

Unsloth: Merging LoRA weights into 4bit model...


/usr/local/lib/python3.12/dist-packages/peft/tuners/lora/bnb.py:397: UserWarning: Merge lora module to 4-bit linear may get different generations due to rounding errors.
  warnings.warn(


Unsloth: Merging finished.
Unsloth: Found skipped modules: ['model.layers.1.mlp.gate_proj', 'model.layers.1.mlp.up_proj', 'model.layers.1.mlp.down_proj', 'lm_head']. Updating config.
Unsloth: Saving merged 4bit model to schmuelling/Llama-3.2-1B-Instruct-finetome...
Unsloth: Merged 4bit model saved.


Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...t-finetome/tokenizer.json: 100%|##########| 17.2MB / 17.2MB            

  ...inetome/model.safetensors:   2%|2         | 24.6MB / 1.10GB            

Unsloth: Merged 4bit model process completed.


In [ ]:
quant_methods = ["q2_k"]
for quant in quant_methods:
    model.push_to_hub_gguf(f"{repo_id}-GGUF", tokenizer, quant)


Unsloth: Converting model to GGUF format...
Unsloth: Merging model weights to 16-bit format...
Found HuggingFace hub cache directory: /root/.cache/huggingface/hub
Checking cache directory for required files...
Cache check failed: model.safetensors not found in local cache.
Not all required files found in cache. Will proceed with downloading.
Checking cache directory for required files...
Cache check failed: tokenizer.model not found in local cache.
Not all required files found in cache. Will proceed with downloading.


Unsloth: Preparing safetensor model files:   0%|          | 0/1 [00:00<?, ?it/s]

model.safetensors:   0%|          | 0.00/2.47G [00:00<?, ?B/s]

Unsloth: Preparing safetensor model files: 100%|██████████| 1/1 [00:06<00:00,  6.83s/it]


Note: tokenizer.model not found (this is OK for non-SentencePiece models)


Unsloth: Merging weights into 16bit: 100%|██████████| 1/1 [00:07<00:00,  7.90s/it]


Unsloth: Merge process complete. Saved to `/tmp/unsloth_gguf_0bx4l0y8`
Unsloth: Converting to GGUF format...
==((====))==  Unsloth: Conversion from HF to GGUF information
   \\   /|    [0] Installing llama.cpp might take 3 minutes.
O^O/ \_/ \    [1] Converting HF to GGUF bf16 might take 3 minutes.
\        /    [2] Converting GGUF bf16 to ['q2_k'] might take 10 minutes each.
 "-____-"     In total, you will have to wait at least 16 minutes.

Unsloth: llama.cpp found in the system. Skipping installation.
Unsloth: Preparing converter script...
Unsloth: [1] Converting model into bf16 GGUF format.
This might take 3 minutes...


RuntimeError: Failed to convert model to GGUF: Unsloth: GGUF conversion failed: Unsloth: Failed to convert model to GGUF: Command 'python llama.cpp/unsloth_convert_hf_to_gguf.py --outfile llama-3.2-1b-instruct.BF16.gguf --outtype bf16 --split-max-size 50G /tmp/unsloth_gguf_0bx4l0y8' returned non-zero exit status 1.

In [ ]:
from huggingface_hub import HfApi, create_repo

create_repo(repo_id=repo_id, token=HF_TOKEN, exist_ok=True)

api = HfApi()
api.upload_folder(
    folder_path=repo_id,
    repo_id=repo_id,
    token=HF_TOKEN,
)